In [1]:
#%load_ext sparksql_magic
from pyspark.sql import SparkSession
from pyspark.sql.functions import expr, col

In [2]:
spark = (
    SparkSession.builder.appName("dim_repo")
    .config("spark.executor.memory", "16g")  
    .config("spark.driver.memory", "16g")  
    .getOrCreate()
)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/03/17 16:53:28 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
25/03/17 16:53:29 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [3]:
for key, value in spark.sparkContext.getConf().getAll():
    if "memory" in key or "executor" in key:
        print(f"{key} = {value}")

spark.executor.memory = 16g
spark.executor.id = driver
spark.driver.memory = 16g
spark.executor.extraJavaOptions = -Djava.net.preferIPv6Addresses=false -XX:+IgnoreUnrecognizedVMOptions --add-opens=java.base/java.lang=ALL-UNNAMED --add-opens=java.base/java.lang.invoke=ALL-UNNAMED --add-opens=java.base/java.lang.reflect=ALL-UNNAMED --add-opens=java.base/java.io=ALL-UNNAMED --add-opens=java.base/java.net=ALL-UNNAMED --add-opens=java.base/java.nio=ALL-UNNAMED --add-opens=java.base/java.util=ALL-UNNAMED --add-opens=java.base/java.util.concurrent=ALL-UNNAMED --add-opens=java.base/java.util.concurrent.atomic=ALL-UNNAMED --add-opens=java.base/jdk.internal.ref=ALL-UNNAMED --add-opens=java.base/sun.nio.ch=ALL-UNNAMED --add-opens=java.base/sun.nio.cs=ALL-UNNAMED --add-opens=java.base/sun.security.action=ALL-UNNAMED --add-opens=java.base/sun.util.calendar=ALL-UNNAMED --add-opens=java.security.jgss/sun.security.krb5=ALL-UNNAMED -Djdk.reflect.useDirectMethodHandle=false


In [4]:
df = spark.read.json("/data/*.json.gz")
# Filter for IssuesEvent
df = df.filter(df["type"] == "IssuesEvent")
df = df.select(
    col("actor"),
    col("created_at"),
    col("id").alias("event_id"),
    col("org"),
    col("repo"),
    col("payload.action"),
    col("payload.issue")
).cache()
df.createOrReplaceTempView("df")
df.count() # Force cache to memory 

25/03/17 16:53:44 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.
                                                                                

47917

## For github repo dim data


In [5]:
%%sql
INSERT OVERWRITE TABLE iceberg.dim_repo
SELECT DISTINCT
  CAST(repo.id AS BIGINT) AS id,
  repo.name,
  repo.url
FROM
  df;

25/03/17 16:53:53 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.
                                                                                

++
||
++
++

In [6]:
%%sql 
SELECT
  *
FROM
  iceberg.dim_repo

+-----------+--------------------------------------------------------+-------------------------------------------------------------------------------------+
|        id |                                                   name |                                                                                 url |
+-----------+--------------------------------------------------------+-------------------------------------------------------------------------------------+
| 716240168 |                          AshwinAnand868/car-rental-app |                          https://api.github.com/repos/AshwinAnand868/car-rental-app |
| 291473513 |                VolkovLabs/volkovlabs-dynamictext-panel |                https://api.github.com/repos/VolkovLabs/volkovlabs-dynamictext-panel |
| 704981549 |                                  rainflame/pika-routes |                                  https://api.github.com/repos/rainflame/pika-routes |
| 103769370 |                                        rvlenth/emmeans |                                        https://api.github.com/repos/rvlenth/emmeans |
| 582137397 |                        ASJordi/website-activity-status |                        https://api.github.com/repos/ASJordi/website-activity-status |
|  67305738 |                                            dtolnay/syn |                                            https://api.github.com/repos/dtolnay/syn |
| 713640829 |                                          eryjus/16bcfs |                                          https://api.github.com/repos/eryjus/16bcfs |
| 619931831 |                                      wlky-0106/upptime |                                      https://api.github.com/repos/wlky-0106/upptime |
|  35810174 |  electron-react-boilerplate/electron-react-boilerplate |  https://api.github.com/repos/electron-react-boilerplate/electron-react-boilerplate |
| 736471558 |                               DanielKim7305/first_repo |                               https://api.github.com/repos/DanielKim7305/first_repo |
| 671269505 |                                        BerriAI/litellm |                                        https://api.github.com/repos/BerriAI/litellm |
| 589055547 |                           chickensoft-games/SuperNodes |                           https://api.github.com/repos/chickensoft-games/SuperNodes |
| 559150595 |                                          emoss08/Monta |                                          https://api.github.com/repos/emoss08/Monta |
| 228040072 |                hyttysmyrkky/node-red-contrib-vestel-tv |                https://api.github.com/repos/hyttysmyrkky/node-red-contrib-vestel-tv |
| 315330275 |                                    n00mkrad/flowframes |                                    https://api.github.com/repos/n00mkrad/flowframes |
| 266574355 |                                      Enubia/ghost-chat |                                      https://api.github.com/repos/Enubia/ghost-chat |
| 646659981 |                 nicedouble/StreamlitAntdComponentsDemo |                 https://api.github.com/repos/nicedouble/StreamlitAntdComponentsDemo |
| 312702579 |                 theepiccode/Awesome-CyberSec-Resources |                 https://api.github.com/repos/theepiccode/Awesome-CyberSec-Resources |
| 664620196 |         UMC-CommonPlant/CommonPlant-Server-Refactoring |         https://api.github.com/repos/UMC-CommonPlant/CommonPlant-Server-Refactoring |
| 202436160 |                                    blackjid/k8s-gitops |                                    https://api.github.com/repos/blackjid/k8s-gitops |
| 736076870 |                                   Colpr/Elike-mainsite |                                   https://api.github.com/repos/Colpr/Elike-mainsite |
| 320758273 |                                 goorm-dev/goorm-status |                                 https://api.github.com/repos/goorm-dev/goorm-status |
| 161012019 |                                      jellyfin/jellyfin |     

## For github organization data

In [7]:
%%sql
INSERT OVERWRITE TABLE iceberg.dim_org
SELECT DISTINCT
  CAST(org.id AS BIGINT) AS id,
  org.login AS name,
  org.url
FROM
  df
WHERE
  org.id IS NOT NULL;

++
||
++
++

In [8]:
%%sql
SELECT
  *
FROM
  iceberg.dim_org

+-----------+------------------------------------+----------------------------------------------------------------+
|        id |                               name |                                                            url |
+-----------+------------------------------------+----------------------------------------------------------------+
|  63673944 |                            EchoMTG |                            https://api.github.com/orgs/EchoMTG |
| 109387420 |                       skypilot-org |                       https://api.github.com/orgs/skypilot-org |
|    107424 |                          jenkinsci |                          https://api.github.com/orgs/jenkinsci |
| 115095870 |                           geoarrow |                           https://api.github.com/orgs/geoarrow |
|  46011144 |                    emscripten-core |                    https://api.github.com/orgs/emscripten-core |
|  13117366 |                            Genivia |                            https://api.github.com/orgs/Genivia |
|  86002201 |                        AppFlowy-IO |                        https://api.github.com/orgs/AppFlowy-IO |
|    499557 |                          Ultimaker |                          https://api.github.com/orgs/Ultimaker |
| 116743741 | Peace-Research-Institute-Frankfurt | https://api.github.com/orgs/Peace-Research-Institute-Frankfurt |
|  53302311 |                       tachiyomiorg |                       https://api.github.com/orgs/tachiyomiorg |
|  42786462 |                           glygener |                           https://api.github.com/orgs/glygener |
| 146737021 |                    XMOJ-Script-dev |                    https://api.github.com/orgs/XMOJ-Script-dev |
|  71887432 |                           atrocore |                           https://api.github.com/orgs/atrocore |
|   6175168 |                          webcompat |                          https://api.github.com/orgs/webcompat |
| 150616486 |                      teslamate-org |                      https://api.github.com/orgs/teslamate-org |
|  33450111 |                          snakemake |                          https://api.github.com/orgs/snakemake |
|  42523220 |                        DroneBridge |                        https://api.github.com/orgs/DroneBridge |
|  78280412 |                          themoeway |                          https://api.github.com/orgs/themoeway |
|  34724717 |                            serpapi |                            https://api.github.com/orgs/serpapi |
|   6432223 |                  Darkhax-Minecraft |                  https://api.github.com/orgs/Darkhax-Minecraft |
|   1378700 |                          Excel-DNA |                          https://api.github.com/orgs/Excel-DNA |
|  93217840 |                     DeebotUniverse |                     https://api.github.com/orgs/DeebotUniverse |
| 107296090 |                        ARBProtocol |                        https://api.github.com/orgs/ARBProtocol |
|  35700027 |                          BuilderIO |                          https://api.github.com/orgs/BuilderIO |
|  13883425 |                          goorm-dev |                          https://api.github.com/orgs/goorm-dev |
|   5400834 |                            keybase |                            https://api.github.com/orgs/keybase |
|  60380796 |                          XmacsLabs |                          https://api.github.com/orgs/XmacsLabs |
|  45900272 |                          Canardoux |                          https://api.github.com/orgs/Canardoux |
|  31827903 |                      deliciousmods |                      https://api.github.com/orgs/deliciousmods |
|   3380462 |                         prometheus |                         https://api.github.com/orgs/prometheus |
|  54536011 |                         tauri-apps |                         https://api.github.com/orgs/tauri-apps |
|  11790256 |                             formio |      

## fct_issue_events (github issue events)

In [9]:
%%sql
INSERT OVERWRITE TABLE iceberg.fct_issue_event
SELECT
  -- Primary Key & Event Type
  CAST(event_id AS BIGINT) AS event_id, -- Unique event ID
  action, -- Event type (created, closed, reopened)
  -- Issue Features (ML Inputs)
  issue.title AS issue_title, -- Issue title
  issue.body AS issue_body, -- Issue description
  issue.author_association, -- Creator's association
  issue.state AS issue_state, -- Current state (open, closed)
  issue.state_reason AS issue_state_reason, -- Reason for state change
  -- Issue Creator Struct
  named_struct (
    'id',
    CAST(issue.user.id AS BIGINT), -- Ensures consistency
    'login',
    issue.user.login,
    'url',
    issue.user.url,
    'is_bot',
    CASE
      WHEN issue.user.type != 'Bot' THEN 0
      ELSE 1
    END
  ) AS issue_creator,
  -- Other Issue Attributes
  CAST(issue.comments AS BIGINT) AS issue_comment_count, -- Number of comments (could be useful)
  CASE
    WHEN issue.assignee IS NOT NULL THEN GREATEST (SIZE (issue.assignees), 1)
    ELSE SIZE (issue.assignees)
  END AS num_assignees, -- Ensures at least 1 if there’s an assignee
  -- Labels (No changes, still TBD)
  issue.labels,
  -- Milestone Struct
  CASE
    WHEN issue.milestone IS NOT NULL THEN named_struct (
      'id',
      CAST(issue.milestone.id AS BIGINT),
      'title',
      issue.milestone.title,
      'description',
      issue.milestone.description,
      'state',
      issue.milestone.state,
      'closed_issues',
      CAST(issue.milestone.closed_issues AS BIGINT),
      'open_issues',
      CAST(issue.milestone.open_issues AS BIGINT),
      'due_on',
      CAST(issue.milestone.due_on AS TIMESTAMP),
      'created_at',
      CAST(issue.milestone.created_at AS TIMESTAMP),
      'updated_at',
      CAST(issue.milestone.updated_at AS TIMESTAMP),
      'closed_at',
      CAST(issue.milestone.closed_at AS TIMESTAMP)
    )
    ELSE NULL
  END AS milestone,
  -- Timestamps (Time-Based Features)
  CAST(issue.created_at AS TIMESTAMP) AS issue_created_at,
  CAST(issue.closed_at AS TIMESTAMP) AS issue_closed_at,
  CAST(issue.updated_at AS TIMESTAMP) AS issue_updated_at,
  CAST(created_at AS TIMESTAMP) AS event_created_at, -- Timestamp when event occurred
  -- Foreign Keys (For Joins, Placed at the End)
  CAST(issue.id AS BIGINT) AS issue_id, -- FK to Issues
  CAST(actor.id AS BIGINT) AS user_id, -- FK to Users
  CAST(org.id AS BIGINT) AS org_id -- FK to Organizations
FROM
  df;

++
||
++
++

In [10]:
%%sql
SELECT
  *
FROM
  iceberg.fct_issue_event

+-------------+----------+----------------------------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------+-------------+--------------------+----------------------------------------------------------------------------------------------------------------------------------------------------+---------------------+---------------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+---------------------+-----------------+---------------------+---------------------+------------+-----------+-----------+
|    event_id |   action |                                                                                                                issue_title |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  issue_body | author_association | issue_state | issue_state_reason |                                                                                                                                      issue_creator | issue_comment_count | num_assignees |                                                                                                                                                                                                                 

In [11]:
spark.stop()